In [1]:
%matplotlib inline
n_epochs_all = None
save_path = 'data/'
show_plot = True

In [2]:
import matplotlib
matplotlib.rcParams["pdf.fonttype"] = 42
matplotlib.rcParams["ps.fonttype"] = 42
import matplotlib.pyplot as plt
from matplotlib.colors import LinearSegmentedColormap
import seaborn as sns

import numpy as np
import numpy.random as random
import pandas as pd
import scanpy as sc
import louvain

use_cuda = True
from scvi.dataset.dataset import GeneExpressionDataset
from scvi.inference import UnsupervisedTrainer
from scvi.models import SCANVI, VAE


from umap import UMAP

[2019-10-28 11:22:04,284] INFO - scvi._settings | Added StreamHandler with custom formatter to 'scvi' logger.
/home/solrust/python/lib/python3.7/site-packages/sklearn/utils/linear_assignment_.py:21: DeprecationWarning: The linear_assignment_ module is deprecated in 0.21 and will be removed from 0.23. Use scipy.optimize.linear_sum_assignment instead.
  DeprecationWarning)


In [3]:
from scvi.dataset.csv import CsvDataset

In [70]:
data1 = CsvDataset(filename='/d0/home/solrust/tooth/human_germinectomy.txt', sep='\t')
data1
data2 = CsvDataset(filename='/d0/home/solrust/tooth/human_molar_pulp.txt', sep='\t')
data2
data3 = CsvDataset(filename='/d0/home/solrust/tooth/human_molar_pulp_old.txt', sep='\t')
data3
data4 = CsvDataset(filename='/d0/home/solrust/tooth/human_molar_healthy_2.txt', sep='\t')
data4
data5 = CsvDataset(filename='/d0/home/solrust/tooth/human_molar_healthy_1.txt', sep='\t')
data5
data6 = CsvDataset(filename='/d0/home/solrust/tooth/human_germ_molar_apical_papilla_female_15yo.txt', sep='\t')
data6
data7 = CsvDataset(filename='/d0/home/solrust/tooth/No5_24_yo_healthy_retained.txt', sep='\t')
data7

[2019-10-28 13:20:57,639] INFO - scvi.dataset.csv | Preprocessing dataset
[2019-10-28 13:20:59,796] INFO - scvi.dataset.csv | Finished preprocessing dataset
[2019-10-28 13:20:59,909] INFO - scvi.dataset.dataset | Remapping batch_indices to [0,N]
[2019-10-28 13:20:59,910] INFO - scvi.dataset.dataset | Remapping labels to [0,N]
[2019-10-28 13:20:59,959] INFO - scvi.dataset.dataset | Computing the library size for the new data
[2019-10-28 13:20:59,996] INFO - scvi.dataset.dataset | Downsampled from 1315 to 1315 cells
[2019-10-28 13:20:59,997] INFO - scvi.dataset.dataset | Not subsampling. No parameter given
[2019-10-28 13:20:59,998] INFO - scvi.dataset.csv | Preprocessing dataset
[2019-10-28 13:21:06,237] INFO - scvi.dataset.csv | Finished preprocessing dataset
[2019-10-28 13:21:06,530] INFO - scvi.dataset.dataset | Remapping batch_indices to [0,N]
[2019-10-28 13:21:06,532] INFO - scvi.dataset.dataset | Remapping labels to [0,N]
[2019-10-28 13:21:06,649] INFO - scvi.dataset.dataset | Comp

GeneExpressionDataset object with n_cells x nb_genes = 13208 x 21771
    gene_attribute_names: 'gene_names'
    cell_attribute_names: 'local_means', 'batch_indices', 'labels', 'local_vars'
    cell_categorical_attribute_names: 'batch_indices', 'labels'

In [71]:
all_dataset = GeneExpressionDataset()
all_dataset.populate_from_datasets([data1, data2, data3, data4, data5, data6, data7])

[2019-10-28 13:23:45,120] INFO - scvi.dataset.dataset | Keeping 21771 genes
[2019-10-28 13:23:45,214] INFO - scvi.dataset.dataset | Computing the library size for the new data
[2019-10-28 13:23:45,336] INFO - scvi.dataset.dataset | Remapping batch_indices to [0,N]
[2019-10-28 13:23:45,337] INFO - scvi.dataset.dataset | Remapping labels to [0,N]
[2019-10-28 13:23:45,601] INFO - scvi.dataset.dataset | Computing the library size for the new data
[2019-10-28 13:23:46,661] INFO - scvi.dataset.dataset | Remapping batch_indices to [0,N]
[2019-10-28 13:23:46,663] INFO - scvi.dataset.dataset | Remapping labels to [0,N]
[2019-10-28 13:23:46,714] INFO - scvi.dataset.dataset | Computing the library size for the new data
[2019-10-28 13:23:46,752] INFO - scvi.dataset.dataset | Remapping batch_indices to [0,N]
[2019-10-28 13:23:46,753] INFO - scvi.dataset.dataset | Remapping labels to [0,N]
[2019-10-28 13:23:47,262] INFO - scvi.dataset.dataset | Computing the library size for the new data
[2019-10-28

In [72]:
all_dataset

GeneExpressionDataset object with n_cells x nb_genes = 41673 x 21771
    gene_attribute_names: 'gene_names'
    cell_attribute_names: 'local_means', 'batch_indices', 'labels', 'local_vars'
    cell_categorical_attribute_names: 'batch_indices', 'labels'

In [80]:
all_dataset.subsample_genes(new_n_genes=3000)

[2019-10-28 15:11:04,399] INFO - scvi.dataset.dataset | Downsampling from 4000 to 3000 genes
[2019-10-28 15:11:04,847] INFO - scvi.dataset.dataset | Computing the library size for the new data
[2019-10-28 15:11:05,221] INFO - scvi.dataset.dataset | Filtering non-expressing cells.
[2019-10-28 15:11:05,676] INFO - scvi.dataset.dataset | Computing the library size for the new data
[2019-10-28 15:11:05,839] INFO - scvi.dataset.dataset | Downsampled from 41673 to 41673 cells


In [92]:
data1 = CsvDataset(filename='/d0/home/solrust/tooth/allhuman_germinectomy.txt', sep='\t')
data1
data2 = CsvDataset(filename='/d0/home/solrust/tooth/allhuman_molar_pulp.txt', sep='\t')
data2
data3 = CsvDataset(filename='/d0/home/solrust/tooth/allmouse_incisor_pulp.txt', sep='\t')
data3
data4 = CsvDataset(filename='/d0/home/solrust/tooth/allmouse_molar_pulp.txt', sep='\t')
data4
data5 = CsvDataset(filename='/d0/home/solrust/tooth/allhuman_molar_pulp_old.txt', sep='\t')
data5
data6 = CsvDataset(filename='/d0/home/solrust/tooth/allmouse_molar_SS2.txt', sep='\t')
data6
data7 = CsvDataset(filename='/d0/home/solrust/tooth/allmouse_incisor_SS2.txt', sep='\t')
data7
data8 = CsvDataset(filename='/d0/home/solrust/tooth/allhuman_molar_healthy_2.txt', sep='\t')
data8
data9 = CsvDataset(filename='/d0/home/solrust/tooth/allhuman_molar_healthy_1.txt', sep='\t')
data9
data10 = CsvDataset(filename='/d0/home/solrust/tooth/allhuman_germ_molar_apical_papilla_female_15yo.txt', sep='\t')
data10
data11 = CsvDataset(filename='/d0/home/solrust/tooth/allNo5_24_yo_healthy_retained.txt', sep='\t')
data11
data12 = CsvDataset(filename='/d0/home/solrust/tooth/allMouse_molar_pulp_in_MeOH_11_9_9.txt', sep='\t')
data12

[2019-10-28 17:20:22,799] INFO - scvi.dataset.csv | Preprocessing dataset
[2019-10-28 17:20:24,671] INFO - scvi.dataset.csv | Finished preprocessing dataset
[2019-10-28 17:20:25,054] INFO - scvi.dataset.dataset | Remapping batch_indices to [0,N]
[2019-10-28 17:20:25,055] INFO - scvi.dataset.dataset | Remapping labels to [0,N]
[2019-10-28 17:20:25,091] INFO - scvi.dataset.dataset | Computing the library size for the new data
[2019-10-28 17:20:25,120] INFO - scvi.dataset.dataset | Downsampled from 1315 to 1315 cells
[2019-10-28 17:20:25,121] INFO - scvi.dataset.dataset | Not subsampling. No parameter given
[2019-10-28 17:20:25,122] INFO - scvi.dataset.csv | Preprocessing dataset
[2019-10-28 17:20:29,658] INFO - scvi.dataset.csv | Finished preprocessing dataset
[2019-10-28 17:20:29,822] INFO - scvi.dataset.dataset | Remapping batch_indices to [0,N]
[2019-10-28 17:20:29,824] INFO - scvi.dataset.dataset | Remapping labels to [0,N]
[2019-10-28 17:20:29,888] INFO - scvi.dataset.dataset | Comp

GeneExpressionDataset object with n_cells x nb_genes = 1503 x 15074
    gene_attribute_names: 'gene_names'
    cell_attribute_names: 'local_means', 'batch_indices', 'labels', 'local_vars'
    cell_categorical_attribute_names: 'batch_indices', 'labels'

In [93]:
all_dataset = GeneExpressionDataset()
all_dataset.populate_from_datasets([data1, data2, data3, data4, data5, data6, data7,data8,data9,data10,data11,data12])
all_dataset

[2019-10-28 17:22:45,476] INFO - scvi.dataset.dataset | Keeping 15074 genes
[2019-10-28 17:22:45,526] INFO - scvi.dataset.dataset | Computing the library size for the new data
[2019-10-28 17:22:45,606] INFO - scvi.dataset.dataset | Remapping batch_indices to [0,N]
[2019-10-28 17:22:45,608] INFO - scvi.dataset.dataset | Remapping labels to [0,N]
[2019-10-28 17:22:46,242] INFO - scvi.dataset.dataset | Computing the library size for the new data
[2019-10-28 17:22:46,612] INFO - scvi.dataset.dataset | Remapping batch_indices to [0,N]
[2019-10-28 17:22:46,613] INFO - scvi.dataset.dataset | Remapping labels to [0,N]
[2019-10-28 17:22:46,810] INFO - scvi.dataset.dataset | Computing the library size for the new data
[2019-10-28 17:22:47,047] INFO - scvi.dataset.dataset | Remapping batch_indices to [0,N]
[2019-10-28 17:22:47,048] INFO - scvi.dataset.dataset | Remapping labels to [0,N]
[2019-10-28 17:22:47,075] INFO - scvi.dataset.dataset | Computing the library size for the new data
[2019-10-28

GeneExpressionDataset object with n_cells x nb_genes = 50436 x 15074
    gene_attribute_names: 'gene_names'
    cell_attribute_names: 'local_means', 'batch_indices', 'labels', 'local_vars'
    cell_categorical_attribute_names: 'batch_indices', 'labels'

In [94]:
all_dataset.subsample_genes(new_n_genes=4000)

[2019-10-28 17:24:02,954] INFO - scvi.dataset.dataset | Downsampling from 15074 to 4000 genes
[2019-10-28 17:24:05,419] INFO - scvi.dataset.dataset | Computing the library size for the new data
[2019-10-28 17:24:06,013] INFO - scvi.dataset.dataset | Filtering non-expressing cells.
[2019-10-28 17:24:06,637] INFO - scvi.dataset.dataset | Computing the library size for the new data
[2019-10-28 17:24:06,883] INFO - scvi.dataset.dataset | Downsampled from 50436 to 50436 cells


In [95]:
vae = VAE(all_dataset.nb_genes, n_batch=all_dataset.n_batches, n_labels=all_dataset.n_labels,
          n_hidden=128, n_latent=30, n_layers=2, dispersion='gene')

trainer = UnsupervisedTrainer(vae, all_dataset, train_size=1.0)
#n_epochs = 150 if n_epochs_all is None else n_epochs_all # n_epochs=150 for human samples
n_epochs = 50 if n_epochs_all is None else n_epochs_all # n_epochs=50 for all human and mouse samples
trainer.train(n_epochs=n_epochs)

training: 100%|██████████| 50/50 [38:25<00:00, 46.11s/it]


In [29]:
torch.save(trainer.model.state_dict(),save_path+'harmonization.vae.allgenes.30.model.pkl')

NameError: name 'torch' is not defined

In [96]:
full = trainer.create_posterior(trainer.model, all_dataset, indices=np.arange(len(all_dataset)))

In [97]:
latent, batch_indices, labels = full.sequential().get_latent()

In [98]:
batch_indices = batch_indices.ravel()

In [99]:
latent_u = UMAP(spread=1).fit_transform(latent)

/home/solrust/python/lib/python3.7/site-packages/numba/compiler.py:602: NumbaPerformanceWarning: 
The keyword argument 'parallel=True' was specified but no transformation for parallel execution was possible.

To find out why, try turning on parallel diagnostics, see http://numba.pydata.org/numba-doc/latest/user/parallel.html#diagnostics for help.

File "../../../../../home/solrust/python/lib/python3.7/site-packages/umap/nndescent.py", line 47:
    @numba.njit(parallel=True)
    def nn_descent(
    ^

  self.func_ir.loc))


In [100]:
np.savetxt('/d0/home/solrust/tooth/10x_datasets/latent_all.txt', latent)
np.savetxt('/d0/home/solrust/tooth/10x_datasets/latent_u_all.txt', latent_u)

In [101]:
cm = LinearSegmentedColormap.from_list(
        'my_cm', ['deepskyblue','green',"orange" ,'hotpink'], N=7)
fig, ax = plt.subplots(figsize=(5, 5))
order = np.arange(latent.shape[0])
random.shuffle(order)
ax.scatter(latent_u[order, 0], latent_u[order, 1], 
           c=all_dataset.batch_indices.ravel()[order], 
           cmap=cm, edgecolors='none', s=1)    
plt.axis("on")
fig.set_tight_layout(True)
fig.savefig("/d0/home/solrust/tooth/scr/fig.pdf")

In [102]:
import scanpy as sc
import anndata
post_adata = anndata.AnnData(X=all_dataset.X)
post_adata.obsm["X_scVI"] = latent
sc.pp.neighbors(post_adata, use_rep="X_scVI", n_neighbors=15)
#sc.tl.umap(post_adata, min_dist=0.1)
post_adata.obs['batch'] = np.array([all_dataset.batch_indices[i][0] 
                                   for i in range(post_adata.n_obs)])

/home/solrust/python/lib/python3.7/site-packages/numba/compiler.py:602: NumbaPerformanceWarning: 
The keyword argument 'parallel=True' was specified but no transformation for parallel execution was possible.

To find out why, try turning on parallel diagnostics, see http://numba.pydata.org/numba-doc/latest/user/parallel.html#diagnostics for help.

File "../../../../../home/solrust/python/lib/python3.7/site-packages/umap/nndescent.py", line 47:
    @numba.njit(parallel=True)
    def nn_descent(
    ^

  self.func_ir.loc))


In [103]:
Markers = ["RGS5", "CDH5", "CD14","PLP1","CCL5","CCL3","APOE","POSTN","IGFBP5","IGFBP3"]

In [104]:
Markers = ["RGS5", "CDH5", "CD14","PLP1","CCL5","CCL3","APOE","POSTN","IGFBP5","IGFBP3","EGR1","WISP1"]
count = all_dataset.X
genenames = all_dataset.gene_names
markers = Markers

nrow = (len(markers) // 3 + 1)
figh = nrow * 4
fig = plt.figure(figsize=(10, figh))
for i, x in enumerate(markers):
    if np.sum(genenames == x)==1:
        exprs = count[:, genenames == x].ravel()
        idx = (exprs > 0)
        plt.subplot(nrow, 3, (i + 1))
        plt.scatter(latent_u[:, 0], latent_u[:, 1], c='lightgrey', edgecolors='none', s=5)
        plt.scatter(latent_u[idx, 0], latent_u[idx, 1], c=exprs[idx], cmap=plt.get_cmap('viridis_r'),
                       edgecolors='none', s=3)
        plt.title(x)
        fig.set_tight_layout(True)
fig.savefig("/d0/home/solrust/tooth/scr/fig1.pdf")

In [105]:
Markers = ["GNAl1","SMOC2","SFRP2","GPC3"]
count = all_dataset.X
genenames = all_dataset.gene_names
markers = Markers

nrow = (len(markers) // 3 + 1)
figh = nrow * 4
fig = plt.figure(figsize=(10, figh))
for i, x in enumerate(markers):
    if np.sum(genenames == x)==1:
        exprs = count[:, genenames == x].ravel()
        idx = (exprs > 0)
        plt.subplot(nrow, 3, (i + 1))
        plt.scatter(latent_u[:, 0], latent_u[:, 1], c='lightgrey', edgecolors='none', s=5)
        plt.scatter(latent_u[idx, 0], latent_u[idx, 1], c=exprs[idx], cmap=plt.get_cmap('viridis_r'),
                       edgecolors='none', s=3)
        plt.title(x)
        fig.set_tight_layout(True)
fig.savefig("/d0/home/solrust/tooth/scr/fig2.pdf")